# Trabajo práctico Nº 7: Medio interestelar

Ayuda para los trabajos prácticos de Sistemas Estelares.

Notebook creada por Tomás Ansin (2021) y modificada por G. Ferrero (2022, 2023)


### 1. a) Descargue del Classroom el archivo $\texttt{polarizacion.dat}$ que contiene los datos de polarización en la banda R de un conjunto de estrellas en el campo del *blazar* 1ES 1959+650 (ver [Sosa et al. 2017; S17](https://ui.adsabs.harvard.edu/abs/2017A%26A...607A..49S)).
### b) Usando las ecuaciones (1), (2) y (3) de S17, calcule la polarización $(P)$ y el ángulo de polarización observado $(\theta_{obs})$.
### Tome en cuenta que es necesario corregir los ı́ndices de Stokes observados ($Q_{obs}$ y $U_{obs}$) por la polarización instrumental ($Q_{ins}$ y $U_{ins}$), de acuerdo a las relaciones
### $Q = Q_{obs} - Q_{ins}$
#### y
### $U = U_{obs} - U_{ins}$
### donde $Q_{ins} = 0.029\; \%$ y $U_{ins} = 0.015\: \%$.
### Lleve los ángulos de polarización observados al sistema estándar, aplicando la corrección
### $\theta_s = \theta_{obs} + \Delta\theta$,
### donde $\Delta\theta = 175.1^\circ$


In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
from scipy.optimize import curve_fit
from astropy.io import fits                        # en esta práctica usaremos algunas tareas de astropy 
from astropy.visualization import ZScaleInterval
plt.style.use('../sisest.mplstyle')

Comencemos observando el contenido del archivo polarizacion.dat

Podemos hacerlo aquí con !head o abrirlo aparte con el editor. Notemos que en los comentarios explica los títulos de cada columna.


In [ ]:

!head -n 15 polarizacion.dat

**Contenido de las columnas**: 
- est : número de identificación de las estrellas en la imagen
- F.... : las columnas que empiezan con F contienen flujos
- eF.... : las columnas que empiezan con eF contienen errores en los flujos
- ....O : las columnas que terminan con O se refieren a los rayos ordinarios
- ....E : las que terminan con E se refieren a los rayos extraordinarios
- ..NNN. : los números NNN, divididos por diez, indican el ángulo de la lámina analizadora en el sistema de referencia del instrumento. Por ejemplo: 225 / 10 = 22.5 grados  

Primero importamos la tabla de datos, indicando como índice la columna est (estrella).


In [ ]:

tpol = pd.read_csv('polarizacion.dat', sep='\s+', header=0, comment='#', index_col='est')
tpol.head()


Ahora calculamos las expresiones $R_Q^2$ y $R_U^2$, usando las ecuaciones indicadas. Recordemos que si operamos con las columnas del dataframe, obtendremos columnas ("vectores verticales") que luego podemos usar en otros cálculos.

In [ ]:
rq2 = ########## completar ecuación
ru2 = ########## completar ecuación

# luego calculamos R_Q y R_U

rq = ########## completar ecuación
ru = ########## completar ecuación

# después calculamos los índices de Stokes observados: Q_obs y U_obs

qobs = ########## completar ecuación
uobs = ########## completar ecuación

# ahora corregimos por la polarización instrumental (recordemos que está dada en porcentajes)

qins  = ########## completar con dato lineamientos
uins  = ########## completar con dato lineamientos

qcorr = ########## completar ecuación
ucorr = ########## completar ecuación

# y por último calculamos la polarización

p = ########## completar ecuación


Ahora calculamos el ángulo de polarización y lo pasamos al sistema estándar (Norte = 0°, Este = 90°). 

Prestar atención al calcular el arcotangente. Según la función que se use, puede ser necesario elegir el cuadrante manualmente.

La función arctan2 funciona así:

$\alpha =$ arctan2($\Delta_y, \Delta_x$)  si y sólo si:   $\tan(\alpha) = \Delta_y/\Delta_x$

y elige correctamente el cuadrante del ángulo $\alpha$ 

In [ ]:
# podemos entonces calcular los ángulos de polarización observados

thetaobs = ########## completar ecuación

# y luego pasarlos al sistema estándar

thetastd = ########## completar ecuación

A continuación podemos agregar estos resultados al dataframe.

In [ ]:
tpol['Q'] = qcorr
tpol['U'] = ucorr

### guardamos la polarización en porcentaje

tpol['P'] = p * 100.   

tpol['theta'] = thetastd

# y si queremos ver las columnas que agregamos, podemos hacer

tpol[["Q", "U", "P", "theta"]]


### Ahora algunas ideas para representar la polarización sobre la imagen del campo.

Usamos *fits.open* 

La función *open* devuelve un objeto llamado HDUList que es una colección de objetos HDU, como si fuera una lista. Un HDU (*Header Data Unit*) es la componente de más alto nivel de la estructura de un archivo FITS. Consiste en un *header* y (típicamente) un arreglo de datos o una tabla.

Primero asignamos a una variable el nombre del archivo fits que contiene la imagen.

In [ ]:
img_archivo ='vonC_0053_PRO.fits'     

# Luego, dentro del bloque with abrimos la imagen, generamos un objeto llamado hdr que contiene el header
# y otro llamado data que contiene la imagen

with fits.open(img_archivo) as hdul:  
    hdul.info()                       # con esto miramos las HDU que contiene el archivo
    hdr = hdul[0].header              
    data = hdul[0].data               

#### Podemos mirar el *header* de la imagen para ver qué información contiene. 

In [ ]:
hdr

#### Podemos observar también que la imagen es simplemente un arreglo de dos dimensiones.

In [ ]:
data

#### Observemos qué sucede si graficamos esta matriz directamente, sin aplicar ninguna transformación (o escala). 

In [ ]:
fig = plt.figure(dpi=100)
plt.imshow(data)          # imshow muestra los datos de un arreglo 2D como si fueran una imagen

#### Para poder ver la imagen debemos aplicarle una transformación (una escala) a los datos.

#### Usamos la escala ZScale, que está basada en la escala que usa la aplicación DS9. 

El intervalo a representar estará definido por la función *ZScaleInterval()*


In [ ]:
interval = ZScaleInterval()

# Calculamos los valores de intensidad mínima y máxima de la imagen y los guardamos en variables 

valor_min, valor_max = interval.get_limits(data) 

# ahora graficamos otra vez, pero ahora solamente el rango elegido (mínimo, máximo), usando un mapa de color en gris

fig = plt.figure(figsize=(6,6), dpi=100)

plt.imshow(data, 
           vmin = valor_min,               # esto define el nivel numérico correspondiente al negro
           vmax = valor_max,               # esto define el nivel numérico correspondiente al blanco
           cmap='gray',                    # esto define la paleta de colores 
           origin='lower')                 # esto coloca el pixel con coordenadas (0,0) en la esquina inferior izquierda
plt.show()

Lo que vemos es la suma de dos imágenes, una captura los rayos ordinarios y otra de los extraordinarios.

#### Para superponer vectores a esta imagen se puede utilizar quiver() de pyplot

#### A quiver hay que darle los vectores de la siguiente forma:

### plt.quiver(x, y, dx, dy, scale_units='xy', scale=1) 

#### Donde el par (x, y) es el origen del vector. (dx, dy) son las componentes del vector. Los orígenes de los vectores (o sea las posiciones de las estrellas, están en la tabla xy.dat) Los valores de dx y dy son **divididos** por el número *scale* 
#### scale_units='xy' iguala la escala de los vectores con la de los ejes

Observemos el contenido del archivo xy.dat

In [ ]:
!head xy.dat

Para graficar los vectores de polarización primero importamos el archivo xy.dat con *numpy* y lo separamos en columnas. Así tenemos las posiciones de las estrellas.

Luego, para obtener las componentes de los vectores en las direcciones $x$ e $y$, proyectamos el vector de polarización sobre cada uno de los ejes usando el ángulo de polarización $\theta$.

In [ ]:
estre, x, y = np.loadtxt('xy.dat', unpack=True)

dx = ########## completar ecuación
dy = ########## completar ecuación

# convertimos el array con los números de las estrellas en un array de enteros

estre_int = estre.astype(int)

Ahora graficamos los vectores superpuestos a la imagen.


In [ ]:
fig = plt.figure(figsize=(6,6), dpi=100)

# primero graficamos la imagen

plt.imshow(data, 
           vmin = valor_min, 
           vmax = valor_max, 
           origin='lower', cmap='gray')

# y ahora los vectores

plt.quiver(x, y, dx, dy, scale_units = 'xy', color = 'red', scale = 0.01)

# para poner etiquetas a los vectores

for nom in estre_int:
    posx = x[nom-1]
    posy = y[nom-1]
    plt.text(posx, posy, str(nom), fontsize=10, c='blue')
        
plt.xlim(-100,1100)
plt.ylim(-200, 1230)
plt.show()

Podemos elegir visualmente cuáles son los vectores de polarización que vamos a promediar, estimando cuáles son "promediables". 

Alternativamente, podemos promediar (por separado obviamente) los valores de polarización y sus ángulos. Luego calculamos sus desviaciones estándar ($\sigma$). Y por último elegimos aquellos vectores que se aparten menos de $\sigma$ del valor promedio. Esos son los que promediamos.

En el informe, se debe incluir el valor medio de la polarización, del ángulo y sus desviaciones estándar.


#### 2. En el archivo $\texttt{NGC6250\_pol.dat}$ se encuentran las medidas de polarización en las bandas fotométricas UBVRI de cuatro estrellas del cúmulo abierto NGC 6250. Verifique si es posible ajustar  la ley de Serkowski a dichas medidas. Cuando sea posible, obtenga los valores de la polarización máxima y su correspondiente longitud de onda, para cada caso. ¿Qué puede decir acerca del origen de la polarización medida?

#### En la ley de Serkowski, adopte un valor de $k = 1.15$ (típico para el medio interestelar en nuestra galaxia).

Como de costumbre, primero importamos la tabla de datos.

In [ ]:
pol6250 = pd.read_csv('NGC6250_pol.dat', sep='\s+', header=None, comment='#',
                     names = ['fil', 'lam', 'P1', 'eP1', 'P3', 'eP3', 'P18', 'eP18', 'P19', 'eP19', 'P25', 'eP25'])
pol6250

Luego graficamos los datos de polarización de la primera estrella en función de las longitudes de onda de los filtros. Es importante hacerlo usando barras de error.


In [ ]:

fig = plt.figure(figsize=(6,4), dpi=150)

plt.errorbar(#### completar aquí ####)
plt.legend()
plt.xlabel('$\lambda$ [$\AA$]')
plt.ylabel('$P$ [%]')

A continuación nos conviene definir la función de Swerkowski como una función de python.


In [ ]:
def PS(lam,pmax,lmax) :
    
    ###### completar
    
    return 


#### Y ajustamos usando curve_fit

En este caso puede ser conveniente darle valores iniciales a los parámetros que ajustaremos.

También nos va a convenir asignar los parámetros ajustados a distintas variables.


In [ ]:
coef, cov = curve_fit( ######## completar ########## )

Como siempre, a continuación es bueno graficar los datos de la tabla junto con el ajuste.

Para eso, recordemos que siempre hay que crear un vector sobre el cual muestrear la función a graficar.


In [ ]:
# por ejemplo así:

longon = np.linspace(3500.,8500.,100)

Y luego graficamos.

In [ ]:
fig = plt.figure(figsize=(6,4), dpi=150)

plt.errorbar( ######## completar ########## )
    
plt.plot(longon, 
         PS(longon,pmax1,lmax1) )

plt.xlabel('$\lambda$ [$\AA$]')
plt.ylabel('$P$ [%]')
plt.legend()
plt.show()

Hay que graficar una por una cada estrella con su ajuste y ver si tiene sentido.